# L'algorithme de Gram-Schmidt

Marc Lorenzi

20 juin 2021

In [ ]:
from sympy import *
init_printing()

# 1. Le théorème de Gram-Schmidt

Soit $E$ un $\mathbb R$-espace vectoriel de dimension finie $n$ muni d'un produit scalaire $<\bullet ,\bullet>$. Soit $\mathcal B=(e_0,e_1,\ldots,e_{n-1})$ une base de $E$. On fabrique par récurrence forte sur $k$ une famille $\mathcal B'=(u_0,u_1,\ldots,u_{n-1})$ de vecteurs de $E$ en posant :

- $u_0=e_0$.
- Pour $1\le k\le n-1$, 

$$u_k=e_k-\sum_{j=0}^{k-1}\frac{<e_k,u_j>}{<u_j, u_j>}u_j$$

__Théorème__ : $\mathcal B'$ est une base orthogonale de $E$, vérifiant de plus $\forall k\in[0,n-1], Vect(u_0,\ldots,u_k)=Vect(e_0,\ldots,e_k)$.

__Démonstration__ : elle se trouve dans tous les bons cours de mathématiques :-).

# 2. L'algorithme

### 2.1 La fonction `gram_schmidt`

Écrivons la fonction `gram_schmidt`. Elle prend en paramètre une base $\mathcal B$ de notre espace vectoriel $E$. Oui, mais c'est qui, $E$ ? Il faut assi passer $E$ en paramètre, d'une façon ou d'une autre. Si on regarde bien les formules de Gram-Schmidt, on voit qu'on a besoin

- du produit scalaire
- de la soustraction dans $E$
- de la multiplication d'un vecteur de $E$ par un réel

Nous allons donc représenter $E$ par un triplet `(ps, sub, mul)` de trois fonctions. L'écriture de l'algorithme est alors immédiate.

In [ ]:
def gram_schmidt(B, E):
    ps, sub, mul = E
    n = len(B)
    B1 = [B[0]]
    for k in range(1, n):
        u = B[k]
        for j in range(k):
            mu = ps(B[k], B1[j]) / ps(B1[j], B1[j])
            u = sub(u, mul(mu, B1[j]))
        B1.append(u)
    return B1

Et voici une fonction qui renvoie `True` lorsque la base $\mathcal B$ est orthogonale.

In [ ]:
def est_orthogonale(B, E):
    n = len(B)
    ps = E[0]
    for i in range(n):
        for j in range(n):
            if j != i and ps(B[i], B[j]) != 0: return False
    return True

### 2.2 Orthonormalisation

Si l'on veut une base orthonormée, il suffit évidemment d'appliquer Gram-Schmidt puis de diviser les vecteurs de la base obtenue par leur norme.

La fonction `normaliser` prend en paramètre un vecteur $u$ et renvoie $u/||u||$.

In [ ]:
def normaliser(u, E):
    ps, sub, mul = E
    return mul(1 / sqrt(ps(u, u)), u)

La fonction `orthonormer` prend en paramètre une base orthogonale $\mathcal B$. Elle renvoie une base orthonormée. 

In [ ]:
def orthonormer(B, E):
    return [normaliser(u, E) for u in B]

### 2.3 Complexité

Nous appelons dans ce qui suit « opération » toute opération sur des réels (addition, multiplication, etc.). Notons 

- $C_p(E)$ le nombre d'opérations nécéssaires pour effectuer le produit scalaire de deux vecteurs de $E$.
- $C_s(E)$ le nombre d'opérations nécéssaires pour effectuer le produit d'un vecteur  de $E$ par un réel.
- $C_m(E)$ le nombre d'opérations nécéssaires pour effectuer la soustraction de deux vecteurs de $E$.

La fonction `gram_schmidt` présente deux boucles imbriquées. La boucle indexée par $k$ effectue $n-1$ itérations, où $n$ est la dimension de $E$. Pour chaque $k$, la boucle indexée par $j$ effectue $k$ itérations. Le nombre total d'itérations est donc
$$\sum_{k=1}^{n-1}k=\frac 1 2 n(n-1)$$

À chaque itération la fonction effectue :

- 2 produits scalaires (on pourrait faire mieux en mémorisant certains résultats)
- 1 soustraction
- 1 produit par un scalaire
- 1 division

Tout cela ne dépend ni de $j$ ni de $k$. Si l'on note, avec un peu de redondance, $C_n(E)$ la complexité de l'algorithme de Schmidt, on a donc
$$C_n(E)=\frac 1 2 n(n-1) (2C_p(E) + C_s(E) + C_m(E) + 1)$$

On ne peut pas aller plus loin dans le cas général : tout dépend de l'espace $E$ sur lequel on travaille. Regardons deux exemples.

# 3. Exemples

### 3.1 $\mathbb R^n$

Munissons $\mathbb R^n$ du produit scalaire canonique. Comme `sympy` sait faire des produits scalaires, soustraire des vecteurs et les multiplier par un réel, il n'y a rien à définir.

Voici $\mathbb R^n$ :

In [ ]:
E1 = (
    lambda u, v: u.dot(v),
    lambda u, v: u - v,
    lambda t, u: t * u)

Faisons quelques tests.

In [ ]:
ps1 = E1[0]
ps1(Matrix([1,2,3]), Matrix([4,5,6]))

In [ ]:
sub1 = E1[1]
sub1(Matrix([1, 2, 3]), Matrix([2, 1, 4]))

Considérons la base $((1, 2, 3), (4, 5,6), (7, 8, 8))$.

In [ ]:
B1 = [Matrix([1, 2, 3]), Matrix([4, 5, 6]), Matrix([7, 8, 8])]
B1

Orthogonalisons.

In [ ]:
B2 = gram_schmidt(B1, E1)
B2

La base est-elle bien orthogonale ?

In [ ]:
est_orthogonale(B2, E1)

Tant que nous y sommes, orthonormalisons.

In [ ]:
orthonormer(B2, E1)

Quelle est la complexité de l'algorithme ?

- Pour effectuer un produit scalaire dans $\mathbb R^n$, on fait $n$ multiplications de réels et $n-1$ additions de réels. Donc, $C_p=2n-1$.
- $C_s=n$ et $C_m=n$, de façon évidente. 

Ainsi, 

$$2C_p+C_s+C_m+1=4n-2+n+n+1=6n-1$$

et 

$$C(n)=\frac 1 2 n(n-1)(6n-1)$$

Ainsi,

$$C(n)\sim 3n^3$$

### 3.2 $\mathbb R_n[X]$

Il existe beaucoup de produits scalaires intéressants sur l'espace $\mathbb R[X]$. Nous allons choisir celui défini par 
$$<P, Q>=\int_{-1}^1P(t)Q(t)\,dt$$ 

In [ ]:
X = Symbol('X')

In [ ]:
E2 = (
    lambda P, Q: integrate(P * Q, (X, -1, 1)),
    lambda P, Q: P - Q,
    lambda t, P: t * P
)

Prenons la base canonique de $\mathbb R_4[X]$.

In [ ]:
B3 = [1, X, X ** 2, X ** 3, X ** 4]

In [ ]:
B4 = gram_schmidt(B3, E2)
B4

In [ ]:
est_orthogonale(B4, E2)

Et orthonormalisons.

In [ ]:
orthonormer(B4, E2)

In [ ]:
list(map(simplify, _))

Les polynômes que nous obtenons font partie d'une famille importante, ils sont appelés les __polynômes de Legendre__.

Quelle est ici la complexité de `gram_schmidt` ? Plaçons nous dans $\mathbb R_n[X]$. On a $C_s=C_m=n+1$ puisque soustraction et produit par un réel se font par des soustractions ou multiplications coefficient par coefficient.

Concernant $C_p$, je n'ai évidemment pas la moindre idée de la complexité de la fonction d'intégration de `sympy`. Cela dit, si l'on code soi-même les calculs d'intégrales, il faut, pour calculer $\int_{-1}^1 PQ$ :

- Multiplier $P$ et $Q$ : cela donne, si on utilise la définition du produit de deux polynômes, $O(n^2)$ opérations élémentaires. On peut calculer précisément cette complexité, mais n'entrons pas dans les détails.
- Intégrer terme à terme : $O(n)$ opérations.

Ainsi, $C_p=O(n^2)$, donc 

$$2C_p+C_s+C_m+1=O(n^2)$$

et

$$C(n)=O(n^4)$$